In [ ]:
import nest_asyncio
nest_asyncio.apply()

from hddCRP.simulations import simulate_sessions
from hddCRP.modelBuilder import cdCRP
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sb

import arviz as az

import os

In [ ]:


simulation_range = [0,1,2,3]
min_blocks = 1;
max_blocks = 10;
block_range = range(min_blocks, max_blocks+1)
run_range = range(0, 20)

results_directory = "Results/Simulations/"
OVERWRITE = False;


if(not os.path.exists(results_directory)):
    os.makedirs(results_directory)

nback_depth   = 1;
context_depth = 2;



In [3]:


for simulation_id in simulation_range:

    if(simulation_id == 0):
        alpha = 2
        different_context_weights = [0.7, 0.7];
        within_session_timescales  = {"A" : 20}
        between_session_timescales = {("A","A") : 2}
        repeat_bias_1_back = 0.75

        session_labels  = lambda n_blocks : ["A"] ;
        session_lengths = lambda n_blocks : [50 * n_blocks];
        num_subjects    = lambda n_blocks : 1;
        num_responses = 3
    elif(simulation_id == 1):
        alpha = 8
        different_context_weights = [0.3, 0.3];
        within_session_timescales  = {"A" : 40}
        between_session_timescales = {("A","A") : 2}
        repeat_bias_1_back = 0.25

        session_labels  = lambda n_blocks : ["A"] ;
        session_lengths = lambda n_blocks : [50 * n_blocks];
        num_subjects = lambda n_blocks : 1;
        num_responses = 3
    elif(simulation_id == 2):
        alpha = 2
        different_context_weights = [0.7, 0.7];
        within_session_timescales  = {"A" : 20}
        between_session_timescales = {("A","A") : 2}
        repeat_bias_1_back = 0.75

        session_labels  = lambda n_blocks : ["A"] ;
        session_lengths = lambda n_blocks : [50 ];
        num_subjects = lambda n_blocks : n_blocks;
        num_responses = 3
    elif(simulation_id == 3):
        alpha = 8
        different_context_weights = [0.3, 0.3];
        within_session_timescales  = {"A" : 40}
        between_session_timescales = {("A","A") : 2}
        repeat_bias_1_back = 0.25

        session_labels  = lambda n_blocks : ["A"] ;
        session_lengths = lambda n_blocks : [50 ];
        num_subjects = lambda n_blocks :  n_blocks;
        num_responses = 3
    elif(simulation_id == 4):
        alpha = 2
        different_context_weights = [0.7, 0.7];
        within_session_timescales  = {"A" : 40}
        between_session_timescales = {("A","A") : 2}
        repeat_bias_1_back = 0.75

        session_labels  = lambda n_blocks : ["A"] ;
        session_lengths = lambda n_blocks : [50 ];
        num_subjects = lambda n_blocks : n_blocks;
        num_responses = 3
    elif(simulation_id == 5):
        alpha = 8
        different_context_weights = [0.3, 0.3];
        within_session_timescales  = {"A" : 20}
        between_session_timescales = {("A","A") : 2}
        repeat_bias_1_back = 0.25

        session_labels  = lambda n_blocks : ["A"] ;
        session_lengths = lambda n_blocks : [50 ];
        num_subjects = lambda n_blocks :  n_blocks;
        num_responses = 3
    else:
        raise NotImplementedError("No sim found")
    
    if(nback_depth < 1):
        repeat_bias_1_back = 1;
    different_context_weights = different_context_weights[:context_depth]

    for block_idx in block_range:
        print(f"BLOCK {block_idx}")
        fit_file = f"{results_directory}/sim_{simulation_id}_block_{block_idx}"
        fit_summary_file = f"{results_directory}/sim_summary_{simulation_id}_block_{block_idx}"
        if(nback_depth != 1 or context_depth != 2):
            fit_file += f"_cd{context_depth}_nb{nback_depth}"
            fit_summary_file  += f"_cd{context_depth}_nb{nback_depth}"


        if(((not os.path.isfile(fit_file)) or (not os.path.isfile(fit_summary_file))) or OVERWRITE):
            simulation_fits = pd.DataFrame()
            simulation_fit_metrics = pd.DataFrame()
            for run_idx in run_range:
                print(f"BLOCK {block_idx} - RUN {run_idx}")
                sim_seed  = (simulation_id+1) * 10000 + run_idx*100
                stan_seed = (simulation_id+1) * 10000 + run_idx*100 + block_idx
                # sim_rng = np.random.Generator(np.random.MT19937(sim_seed))
                
                seqs = [];
                subject_labels = [];
                session_labels_all = [];
                for jj in range(num_subjects(block_idx)):
                    sim_rng = np.random.Generator(np.random.MT19937(sim_seed + jj))
                    seqs_c = simulate_sessions(session_lengths=session_lengths(block_idx), session_labels=session_labels(block_idx), num_responses=num_responses, 
                                            alpha=alpha,
                                            different_context_weights=different_context_weights,
                                            within_session_timescales=within_session_timescales, between_session_timescales=between_session_timescales,
                                            repeat_bias_1_back=repeat_bias_1_back, rng=sim_rng)
                    subject_labels += [jj] * len(seqs_c)
                    session_labels_all += session_labels(block_idx)
                    seqs += seqs_c;

                model = cdCRP(seqs, subject_labels=subject_labels, session_labels=session_labels_all);
                model.same_nback_depth = nback_depth;
                model.context_depth = context_depth;
                
                model.context_depth = len(different_context_weights)
                model.build(random_seed=stan_seed);
                model.fit_model()

                map_fit = model.get_map()
                fit_df = model.fit.to_frame()
                fit_df["block"] = block_idx
                fit_df["run"]   = run_idx
                fit_df["simulation"]   = simulation_id
                summary_df = model.fit_summary()
                summary_df["block"] = block_idx
                summary_df["run"]   = run_idx
                summary_df["MAP"] = pd.Series(map_fit)
                summary_df["simulation"]   = simulation_id

                true_param = {"alpha" : alpha,
                "timeconstant_within_session_A" : within_session_timescales["A"]}
                if(nback_depth >= 1):
                    true_param["repeat_bias_1_back"] = repeat_bias_1_back
                if(nback_depth >= 1):
                    true_param["context_similarity_depth_1"] = different_context_weights[0],
                if(nback_depth >= 21):
                    true_param["context_similarity_depth_2"] = different_context_weights[1]

                summary_df["true"] = pd.Series(true_param)
                

                simulation_fit_metrics = pd.concat([simulation_fit_metrics,summary_df], copy=False)
                simulation_fits = pd.concat([simulation_fits,fit_df], copy=False)

            simulation_fits.to_pickle(fit_file)
            simulation_fit_metrics.to_pickle(fit_summary_file)
        else:
            print("Fit files found: not overriding")


Sampling:  75% (6000/8000)
Sampling:  76% (6100/8000)
Sampling:  78% (6200/8000)
Sampling:  79% (6300/8000)
Sampling:  80% (6400/8000)
Sampling:  81% (6500/8000)
Sampling:  82% (6600/8000)
Sampling:  84% (6700/8000)
Sampling:  85% (6800/8000)
Sampling:  86% (6900/8000)
Sampling:  88% (7000/8000)
Sampling:  89% (7100/8000)
Sampling:  90% (7200/8000)
Sampling:  91% (7300/8000)
Sampling:  92% (7400/8000)
Sampling:  94% (7500/8000)
Sampling:  95% (7600/8000)
Sampling:  96% (7700/8000)
Sampling:  98% (7800/8000)
Sampling:  99% (7900/8000)
Sampling: 100% (8000/8000)
Sampling: 100% (8000/8000), done.
Messages received during sampling:
  Gradient evaluation took 0.016408 seconds
  1000 transitions using 10 leapfrog steps per transition would take 164.08 seconds.
  Adjust your expectations accordingly!
  Informational Message: The current Metropolis proposal is about to be rejected because of the following issue:
  Exception: gamma_lpdf: Random variable is 0, but must be positive finite! (in '

BLOCK 6 - RUN 18
Building...



Building: found in cache, done.Messages from stanc:
    means either no prior is provided, or the prior(s) depend on data
    variables. In the later case, this may be a false positive.
    prior is provided, or the prior(s) depend on data variables. In the later
    case, this may be a false positive.
    either no prior is provided, or the prior(s) depend on data variables. In
    the later case, this may be a false positive.
    either no prior is provided, or the prior(s) depend on data variables. In
    the later case, this may be a false positive.
    provided, or the prior(s) depend on data variables. In the later case,
    this may be a false positive.
Sampling:   0%
Sampling:   0% (1/8000)
Sampling:   0% (2/8000)
Sampling:   0% (3/8000)
Sampling:   0% (4/8000)
Sampling:   1% (103/8000)
Sampling:   3% (202/8000)
Sampling:   4% (301/8000)
Sampling:   5% (400/8000)
Sampling:   6% (500/8000)
Sampling:   8% (600/8000)
Sampling:   9% (700/8000)
Sampling:  10% (800/8000)
Sampling:  

BLOCK 6 - RUN 19
Building...



Building: found in cache, done.Messages from stanc:
    means either no prior is provided, or the prior(s) depend on data
    variables. In the later case, this may be a false positive.
    prior is provided, or the prior(s) depend on data variables. In the later
    case, this may be a false positive.
    either no prior is provided, or the prior(s) depend on data variables. In
    the later case, this may be a false positive.
    either no prior is provided, or the prior(s) depend on data variables. In
    the later case, this may be a false positive.
    provided, or the prior(s) depend on data variables. In the later case,
    this may be a false positive.
Sampling:   0%
Sampling:   0% (1/8000)
Sampling:   0% (2/8000)
Sampling:   0% (3/8000)
Sampling:   0% (4/8000)
Sampling:   1% (103/8000)
Sampling:   3% (202/8000)
Sampling:   4% (301/8000)
Sampling:   5% (400/8000)
Sampling:   6% (500/8000)
Sampling:   8% (600/8000)
Sampling:   9% (700/8000)
Sampling:  10% (800/8000)
Sampling:  

...


Building: found in cache, done.Messages from stanc:
    means either no prior is provided, or the prior(s) depend on data
    variables. In the later case, this may be a false positive.
    prior is provided, or the prior(s) depend on data variables. In the later
    case, this may be a false positive.
    either no prior is provided, or the prior(s) depend on data variables. In
    the later case, this may be a false positive.
    either no prior is provided, or the prior(s) depend on data variables. In
    the later case, this may be a false positive.
    provided, or the prior(s) depend on data variables. In the later case,
    this may be a false positive.
Sampling:   0%
Sampling:   0% (1/8000)
Sampling:   0% (2/8000)
Sampling:   0% (3/8000)
Sampling:   0% (4/8000)
Sampling:   1% (103/8000)
Sampling:   3% (202/8000)
Sampling:   4% (301/8000)
Sampling:   5% (400/8000)
Sampling:   6% (500/8000)
Sampling:   8% (600/8000)
Sampling:   9% (700/8000)
Sampling:  10% (800/8000)
Sampling:  

BLOCK 10 - RUN 18
Building...



Building: found in cache, done.Messages from stanc:
    means either no prior is provided, or the prior(s) depend on data
    variables. In the later case, this may be a false positive.
    prior is provided, or the prior(s) depend on data variables. In the later
    case, this may be a false positive.
    either no prior is provided, or the prior(s) depend on data variables. In
    the later case, this may be a false positive.
    either no prior is provided, or the prior(s) depend on data variables. In
    the later case, this may be a false positive.
    provided, or the prior(s) depend on data variables. In the later case,
    this may be a false positive.
Sampling:   0%
Sampling:   0% (1/8000)
Sampling:   0% (2/8000)
Sampling:   0% (3/8000)
Sampling:   0% (4/8000)
Sampling:   1% (103/8000)
Sampling:   3% (202/8000)
Sampling:   4% (301/8000)
Sampling:   5% (400/8000)
Sampling:   6% (500/8000)
Sampling:   8% (600/8000)
Sampling:   9% (700/8000)
Sampling:  10% (800/8000)
Sampling:  

BLOCK 10 - RUN 19
Building...



Building: found in cache, done.Messages from stanc:
    means either no prior is provided, or the prior(s) depend on data
    variables. In the later case, this may be a false positive.
    prior is provided, or the prior(s) depend on data variables. In the later
    case, this may be a false positive.
    either no prior is provided, or the prior(s) depend on data variables. In
    the later case, this may be a false positive.
    either no prior is provided, or the prior(s) depend on data variables. In
    the later case, this may be a false positive.
    provided, or the prior(s) depend on data variables. In the later case,
    this may be a false positive.
Sampling:   0%
Sampling:   0% (1/8000)
Sampling:   0% (2/8000)
Sampling:   0% (3/8000)
Sampling:   0% (4/8000)
Sampling:   1% (103/8000)
Sampling:   3% (202/8000)
Sampling:   4% (301/8000)
Sampling:   5% (400/8000)
Sampling:   6% (500/8000)
Sampling:   8% (600/8000)
Sampling:   9% (700/8000)
Sampling:  10% (800/8000)
Sampling:  

In [4]:
print(model.model)


data {
    int N; // Number of data points
    int M; // number of possible observations
    array[N] int Y;
    array[N] int local_timeconstant_id;
    array[N] int session_id;
    array[N] real local_time;

    int T; // max observation distance
    int K; // number of subjects that are stacked on top of each other
    array[K+1] int subject_start_idx; // first element should be 1, last element should be N+1

    real prior_alpha_shape;
    real prior_alpha_scale;
    real prior_timeconstant_within_session_shape;
    real prior_timeconstant_within_session_scale;
    matrix[N,T] is_same_context_1;
    real prior_context_similarity_depth_1_alpha;
    real prior_context_similarity_depth_1_beta;
    matrix[N,T] is_same_context_2;
    real prior_context_similarity_depth_2_alpha;
    real prior_context_similarity_depth_2_beta;
    matrix[N,T] is_same_1_back;
    real prior_repeat_bias_1_back_shape;
}

transformed data {
    // variables to turn main computation in matrix operations
    ve